VAMOS A VER QUE PASA CON FOLIUM...      

IMPORTAMOS LIBRERÍAS

In [3]:
import folium
from folium import Choropleth, Circle, Marker, Icon, Map
from folium.plugins import HeatMap, MarkerCluster
import pandas as pd
import time
import requests


IMPORTAMOS EL DF DE UBER EATS 

In [108]:
ue = pd.read_csv("../Data/UberEats.csv", index_col = 0)
ue.head(5)

Restaurante  Valoración  Nota  Delivery_Fee    ETA  \
0  Badsha India Restaurant         200   4.4          1.00  15–35   
1             TUTTO PASTA!          26   2.8          2.50  40–60   
2            Pizza Central          31   3.8          2.99  35–55   
3       Scarlett Real Food          28   3.1          1.90  40–50   
4           La Tagliatella          15   3.9          0.90  25–35   

            Tag Precio                                Dirección  Barrio  
0         India      €             Calle De Embajadores,  28045  Centro  
1  Family Meals      €        Calle De Núñez De Arce, 11, 28012  Centro  
2         Pizza      €  Plaza Del Emperador Carlos V, 10, 28012  Centro  
3       Postres      €                  C/ Preciados 36,  28013  Centro  
4         Pizza      €               Calle De Toledo 27,  28012  Centro

In [5]:
def limp_dir (direccion):
    ole = str(direccion)
    return f'{ole[0:-6]} Madrid'

In [107]:
ue["Dirección"] = ue["Dirección"].apply(limp_dir)
ue.head(5)

Restaurante  Valoración  Nota  Delivery_Fee    ETA  \
0  Badsha India Restaurant         200   4.4          1.00  15–35   
1             TUTTO PASTA!          26   2.8          2.50  40–60   
2            Pizza Central          31   3.8          2.99  35–55   
3       Scarlett Real Food          28   3.1          1.90  40–50   
4           La Tagliatella          15   3.9          0.90  25–35   

            Tag Precio                                  Dirección  Barrio  \
0         India      €             Calle De Embajadores,   Madrid  Centro   
1  Family Meals      €        Calle De Núñez De Arce, 11,  Madrid  Centro   
2         Pizza      €  Plaza Del Emperador Carlos V, 10,  Madrid  Centro   
3       Postres      €                  C/ Preciados 36,   Madrid  Centro   
4         Pizza      €               Calle De Toledo 27,   Madrid  Centro   

        lat       lon  
0  40.40069  -3.69925  
1      None      None  
2  40.40861  -3.69288  
3   0.00000   0.00000  
4      None      None

In [7]:
array = ue[["Dirección"]].to_numpy()

CONVERTIMOS LA COLUMNA DIRECCIONES EN UN ARRAY PARA ITERAR Y CONSEGUIR LAT Y LONG

In [8]:
import json
geo_json = r"../Data/distritos.geojson"

In [9]:
with open (geo_json) as geo_file:
    geo_distritos = json.load(geo_file)

In [10]:
type(geo_distritos)

dict

In [11]:
geo_distritos.keys()

dict_keys(['type', 'features'])

In [12]:
type(geo_distritos["features"])

list

In [13]:
len(geo_distritos["features"])

21

In [14]:
geo_distritos["features"][1]["properties"]["nombre"]

'Moncloa - Aravaca'

In [15]:
geo_distritos["features"][0]["properties"]["nombre"]

'Fuencarral - El Pardo'

In [16]:
datos = {'Fuencarral - El Pardo': 10,
 'Moncloa - Aravaca': 63,
 'Villa de Vallecas': 37,
 'Vicálvaro': 24,
 'Barajas': 33,
 'Hortaleza': 39,
 'Retiro': 114,
 'Moratalaz': 29,
 'Tetuán': 68,
 'Centro': 134,
 'Chamberí': 144,
 'Chamartín': 165,
 'Salamanca': 188,
 'Arganzuela': 109,
 'Carabanchel': 34,
 'Latina': 25,
 'Usera': 29,
 'Puente de Vallecas': 42,
 'Ciudad Lineal': 85,
 'San Blas - Canillejas': 31,
 'Villaverde': 32}

In [17]:
columnas = ["barrio" ,"vol"]

In [149]:
df1 = pd.DataFrame.from_dict(datos, orient="index").reset_index()
df1.columns = columnas
df1

barrio  vol
0   Fuencarral - El Pardo   10
1       Moncloa - Aravaca   63
2       Villa de Vallecas   37
3               Vicálvaro   24
4                 Barajas   33
5               Hortaleza   39
6                  Retiro  114
7               Moratalaz   29
8                  Tetuán   68
9                  Centro  134
10               Chamberí  144
11              Chamartín  165
12              Salamanca  188
13             Arganzuela  109
14            Carabanchel   34
15                 Latina   25
16                  Usera   29
17     Puente de Vallecas   42
18          Ciudad Lineal   85
19  San Blas - Canillejas   31
20             Villaverde   32

In [19]:
distritos_mapa = folium.Map(location=[40.416775, -3.703790], zoom_start=6, tiles="cartodbpositron")# << fantasía tiles='stamenwatercolor'

In [151]:
# generamos el mapa coroplético a modificando el mapa que ya tenemos 
map2 = distritos_mapa.choropleth(
    geo_data = geo_json, #geojson con los polígonos LA RUTA AL ARCHIVO EN MI ORDENADOR
    location = [40.428990,-3.681209], 
    zoom_start = 15,
    data = df1, #dataframe con los datos 
    columns = ["barrio", "vol"], #columnas del dataframe que utilizamos
    key_on = "feature.properties.nombre", # dato geojson polígono de donde salen los nombres TIENE QUE HACER MATCH CON EL DF, 
    fill_color = "YlGnBu", #gama de colores 
    fill_opacity = 0.5, #opacidad del relleno 
    line_opacity = 1.5, #opacidad de la línea
    legend_name = "Volumen de oferta por distrito",  #nombre de la leyenda
    smooth_factor = 1 # suavidad de la línea
)
distritos_mapa

/usr/local/Caskroom/miniconda/base/envs/ironhack/lib/python3.8/site-packages/folium/folium.py:409: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  warnings.warn(


In [154]:
# generamos el mapa coroplético a modificando el mapa que ya tenemos 
distritos_mapa.choropleth(
    geo_data = geo_json, #geojson con los polígonos LA RUTA AL ARCHIVO EN MI ORDENADOR
    location = [40.428990,-3.681209], 
    zoom_start = 15,
    data = df1, #dataframe con los datos 
    columns = ["barrio", "vol"], #columnas del dataframe que utilizamos
    key_on = "feature.properties.nombre", # dato geojson polígono de donde salen los nombres TIENE QUE HACER MATCH CON EL DF, 
    fill_color = "YlGnBu", #gama de colores 
    fill_opacity = 0.5, #opacidad del relleno 
    line_opacity = 1.5, #opacidad de la línea
    legend_name = "Volumen de oferta por distrito",  #nombre de la leyenda
    smooth_factor = 1 # suavidad de la línea
)
distritos_mapa

FUNCIÓN PARA TYPE POINT

In [125]:
donde = "Calle De Núñez De Arce, 11, Madrid	"

In [126]:
data = requests.get(f"https://geocode.xyz/{donde}?json=1").json()
data

{'standard': {'stnumber': '11',
  'addresst': 'Calle de Núñez de Arce',
  'postal': '28012',
  'region': 'Comunidad de Madrid',
  'prov': 'ES',
  'city': 'Madrid',
  'countryname': 'Spain',
  'confidence': '0.90'},
 'longt': '-3.70124',
 'alt': {},
 'elevation': {},
 'latt': '40.41538'}

In [28]:
data["standard"]["addresst"]

{}

In [29]:
data["longt"]

'-3.93779'

In [30]:
data["latt"]

'43.41876'

In [31]:
def geocode(direccion):
    """
    Esta función saca las coordenadas de la dirección que le pases
    """
    data = requests.get(f"https://geocode.xyz/{direccion}?json=1").json()
    try:
        return {"type": "Point", "coordinates": [data["latt"], data["longt"]]}
    except:
        return {"type": "Point", "coordinates": None}

In [35]:
coordenadas = []

In [34]:
coordenadas

[]

In [36]:
for i in ue["Dirección"]:
    time.sleep(2)
    coordenadas.append(geocode(i))

In [38]:
"""for i in ue["Dirección"][634:]:
    time.sleep(2)
    coordenadas.append(geocode(i))"""

'for i in ue["Dirección"][634:]:\n    time.sleep(2)\n    coordenadas.append(geocode(i))'

In [39]:
len(coordenadas)

690

In [40]:
coordenadas[0]

{'type': 'Point', 'coordinates': ['40.40069', '-3.69925']}

In [49]:
coordenadas[0]["coordinates"][0]

'40.40069'

In [50]:
coordenadas[0]["coordinates"][1]

'-3.69925'

In [51]:
lat = []
lon = []

In [113]:
for i in coordenadas:
    try:
        lat.append(i["coordinates"][0])
        lon.append(i["coordinates"][1])
    except:
        lat.append(None)
        lon.append(None)

In [114]:
print(len(lat),len(lon))

1380 1380


In [188]:
lotengo.head(5)

Restaurante  Valoración  Nota  Delivery_Fee    ETA  \
0  Badsha India Restaurant         200   4.4          1.00  15–35   
1             TUTTO PASTA!          26   2.8          2.50  40–60   
2            Pizza Central          31   3.8          2.99  35–55   
3       Scarlett Real Food          28   3.1          1.90  40–50   
4           La Tagliatella          15   3.9          0.90  25–35   

            Tag Precio                                  Dirección  Barrio  \
0         India      €             Calle De Embajadores,   Madrid  Centro   
1  Family Meals      €        Calle De Núñez De Arce, 11,  Madrid  Centro   
2         Pizza      €  Plaza Del Emperador Carlos V, 10,  Madrid  Centro   
3       Postres      €                  C/ Preciados 36,   Madrid  Centro   
4         Pizza      €               Calle De Toledo 27,   Madrid  Centro   

        lat      lon  
0  40.40069 -3.69925  
1  40.41538 -3.70124  
2  40.40861 -3.69288  
3   0.00000  0.00000  
4  40.41377 -3.70737

In [144]:
for i in range(len(lotengo["lat"])):
    try:
        if lotengo["lat"][i] == None:
            print(lotengo["Dirección"][i])
            coordina = geocode(lotengo["Dirección"][i])
            lotengo["lat"][i] = coordina["coordinates"][0]
            lotengo["lon"][i] = coordina["coordinates"][1]
    except:
        pass

In [164]:
lotengo['lat'] = lotengo['lat'].astype(float)

In [166]:
lotengo['lon'] = lotengo['lon'].astype(float)

In [235]:
lotengo.tail(6)

Restaurante  Valoración  Nota  Delivery_Fee    ETA  \
690  Esmirna Doner Kebap          48   4.7           2.4  35–45   
692             Frambons          22   2.7           2.4  35–45   
694     Doner kebap efes          23   4.7           2.4  25–35   
695     Doner kebap efes          30   4.6           1.9  30–40   
698           Sumo Grill          26   4.5           2.9  60–70   
699              Da Yuan         200   4.4           2.9  60–70   

                        Tag Precio                                 Dirección  \
690                   Kebab      €                Calle Zabaleta 1,   Madrid   
692                Empanada      €         Av. Del Mediterráneo, 30,  Madrid   
694                   Kebab      €     Calle De López De Hoyos, 139,  Madrid   
695                   Kebab      €              Calle De Alcalá 205,  Madrid   
698  Opciones para alergias      €     Calle De Ezequiel Solana, 52,  Madrid   
699                   Pasta      €  Calle Del Conde De Peñalver, 66,  Madrid   

            Barrio       lat      lon  
690  Ciudad Lineal  40.44065 -3.67537  
692  Ciudad Lineal  40.40675 -3.67267  
694  Ciudad Lineal  40.44849 -3.66731  
695  Ciudad Lineal  40.44291 -3.61886  
698  Ciudad Lineal  40.43037 -3.64518  
699  Ciudad Lineal  40.43141 -3.67496

In [226]:
lotengo.dropna(axis = 0, how='any', inplace = True)

In [227]:
pd.isna(lotengo["lon"]).sum()

0

In [228]:
print(type(lotengo["lat"][1]),type(lotengo["lon"][1]))

<class 'numpy.float64'> <class 'numpy.float64'>


In [229]:
icono = Icon(color="green",
             opacity=0.3,
             prefix = "fa",
             icon="paw",
             icon_color="black",)

In [230]:
map_2 = Map(location = [40.428990,-3.681209], zoom_start = 13)
map_2

In [233]:
for i,row in lotengo.iterrows():
    distrito = {"location": [row["lat"], row["lon"]], "tooltip": row["Restaurante"]}
    
    if row["Tag"] == "Pizza":
        icono = Icon(color = "red",
                     prefix="fa",
                     icon="laptop",
                     icon_color="black"
        )
    elif row["Tag"] == "Hamburguesa":
        icono = Icon(color = "green",
                     prefix="fa",
                     icon="glass",
                     icon_color="black")
        
    elif row["Tag"] == "Pollo":
        icono = Icon(color = "cadetblue",
                     prefix="fa",
                     icon="bug",
                     icon_color="black")
        
    mark = Marker(**distrito, icon=icono)
    mark.add_to(map_2)
map_2

In [236]:
lotengo.to_csv('definitivo.csv')